# 45-dataset tabular benchmark

Tabular data benchmark from [27]. We used the repository from [27] at https://github.com/LeoGrin/tabular-benchmark, modifying the code as needed to incorporate our method. On all datasets, we grid search over 5 iterations of RFM with the Laplace kernel, solving kernel regression in closed form at all steps. This benchmark consists of 
- 20 medium regression datasets (without categorical variables), 
- 3 large regression datasets (without categorical variables), 
- 15 medium classification datasets (without categorical variables), 
- 4 large classification datasets (without categorical variables), 
- 13 medium classification datasets (with categorical variables), 
- 5 large regression datasets (with categorical variables), 
- 7 medium classification datasets (with categorical variables), and 
- 2 large classification datasets (with categorical variables). 

Following the terminology from [27], “medium” refers to datasets with at most 10000 training examples and “large” refers to those with more than 10000 training examples. 

**Hyperparameter Tuning:** In general [for RFM], we grid-searched over ridge regularization parameters in $\{10^{−4}, 10^{−3}, 10^{−2}, 10^{−1}, 1\}$ with fixed bandwidth $L = 10$. For regression, we centered the labels and scaled their variance to 1. On large regression datasets, we also optimized for bandwidths over $\{1, 5, 10, 15, 20\}$. 

We searched over two target transformations - the log transform $(\hat{y} = |y| log(1 + |y|))$ and `sklearn.preprocessing.QuantileTransformer`. In both cases, we inverted the transform before testing. We also searched over data transformations - `sklearn.preprocessing.StandardScaler` and `sklearn.preprocessing.QuantileTransformer`. We also optimized for the use of centering/not centering the gradients in our computation, and extracting just the diagonal of the feature matrix. For non-kernel methods, we compare to the metrics reported in [27]. 

**Evaluation Scores:** For classification, we report the average accuracy across the random iterations in each sweep (including random train/val/test splits). For regression, the average R2 is reported. The reported test score is the average performance of the model with the highest average validation performance.

| Dataset name | size | features | description |
|--------------|------|----------|-------------|
|california    | 20634 | 8       | https://www.dcc.fc.up.pt/ltorgo/Regression/cal_housing.html%22 |
|Diabetes130US | 71090 | 7       | https://www.openml.org/d/4541 |
| jannis       | 57580 | 54      | https://www.openml.org/search?type=data&sort=runs&id=41168&status=active |
| covertype    | 566602 | 10     | https://www.openml.org/search?type=data&sort=runs&id=293&status=active |
| Higgs	       | 940160 | 24     | https://www.openml.org/search?type=data&sort=runs&id=42769&status=active |

In [1]:
# install using `conda install -c conda-forge line_profiler`
%load_ext line_profiler
%load_ext autoreload
%autoreload 2

In [2]:
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error, accuracy_score
from sklearn.preprocessing import StandardScaler, QuantileTransformer
import numpy as np
import pandas as pd
from copy import deepcopy

# utils for plotting
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.express as px

# utils for kernel ridge regression
from goodpoints.krr.util_estimators import get_estimator, get_sigma_heuristic
# utils for evaluating kernels
from goodpoints.krr.util_k_mmd import kernel_eval, to_regression_kernel
# utils for generate samples from the data distribution
from goodpoints.krr.util_sample import get_Xy #, ToyData , get_toy_dataset, logistic
from goodpoints.krr.util_load_data import get_real_dataset
# utils for dataset thinning
from goodpoints.krr.util_thin import sd_thin, kt_thin2

In [3]:
# add this to be able to render plotly plots in non-vscode notebooks
import plotly.io as pio
pio.renderers.default = "notebook_connected"

In [4]:
# helper functions
def sample(arr, n=1000):
    return arr[np.random.choice(len(arr), n, replace=True)]
def histogram(arr, height=400, width=600):
    return px.histogram(arr, width=width, height=height)

def classification_accuracy(labels, pred):
    decision = pred.copy()
    # implement classification rule
    decision[decision > 0.5] = 1
    decision[decision <= 0.5] = 0
    return accuracy_score(labels, decision)

## Set hyperparameters

In [5]:
### Regression parameters

kernel = 'laplace'  # ['gauss', 'laplace']
sigma = 10
alpha = 1e-3 # 1.0

### RFM parameters
# usually one is enough to learn "reasonable" features
rfm_iters = 1

### Experiment parameters

k_fold = 5      # k >= 2
n_repeats = 10
use_cross_validation = False

n_jobs = 2 # -1 = use all CPUs
save = False

### Thinning parameters

m = None # Thinned dataset will have size n/2**m

In [6]:
# Parameters
n_jobs = 16
n_repeats = 40
save = False
use_cross_validation = True


In [7]:
# Determine auxiliary parameters

task = 'classification'
refit = 'accuracy'
postprocess = 'threshold'
ydim = 1

Kernels:
- RBF:
$$\mathbf{k}(x, y) = \exp(-\gamma ||x-y||_2^2)$$
- Laplacian:
$$\mathbf{k}(x, y) = \exp(-\gamma ||x-y||_1)$$

Median heuristic to choose the bandwidth parameter, i.e., median of squared pairwise distances:
- For Gaussian data, we can compute this exactly. Assume $X\sim \mathcal{N}(0,\sigma^2 I_d)$. For the RBF kernel, $X_1-X_2\sim \mathcal{N}(0,2\sigma^2 I_d)$. Then $(X_1-X_2)^2$ follows a chi-squared distribution with $d$ degrees of freedom, mean $d\cdot \sqrt{2}\sigma$ and median roughly $d(1-\frac{2}{9d})^3 \cdot \sqrt{2}\sigma$. For the Laplacian kernel, $||x-y||_1$ follows a folded normal distribution (https://en.wikipedia.org/wiki/Folded_normal_distribution) with median roughly $\sqrt{2}\sigma$.

Available kernels in sklearn: 
https://scikit-learn.org/stable/modules/classes.html#module-sklearn.metrics.pairwise

## Get dataset

For list of available subsets and their OpenML links:
https://huggingface.co/datasets/inria-soda/tabular-benchmark

```
WARNING:root:Received uncompressed content from OpenML for https://api.openml.org/data/v1/download/22103185/credit.arff.
OpenML Classification Task
==========================
Task Type Description: https://www.openml.org/tt/TaskType.SUPERVISED_CLASSIFICATION
Task ID..............: 361055
Task URL.............: https://www.openml.org/t/361055
Estimation Procedure.: crossvalidation
Evaluation Measure...: predictive_accuracy
Target Feature.......: SeriousDlqin2yrs
# of Classes.........: 2
Cost Matrix..........: Available
WARNING:root:Received uncompressed content from OpenML for https://api.openml.org/data/v1/download/22103245/electricity.arff.
OpenML Classification Task
==========================
Task Type Description: https://www.openml.org/tt/TaskType.SUPERVISED_CLASSIFICATION
Task ID..............: 361060
Task URL.............: https://www.openml.org/t/361060
Estimation Procedure.: crossvalidation
Evaluation Measure...: predictive_accuracy
Target Feature.......: class
# of Classes.........: 2
Cost Matrix..........: Available
WARNING:root:Received uncompressed content from OpenML for https://api.openml.org/data/v1/download/22103246/covertype.arff.
OpenML Classification Task
==========================
Task Type Description: https://www.openml.org/tt/TaskType.SUPERVISED_CLASSIFICATION
Task ID..............: 361061
Task URL.............: https://www.openml.org/t/361061
Estimation Procedure.: crossvalidation
Evaluation Measure...: predictive_accuracy
Target Feature.......: Y
# of Classes.........: 2
Cost Matrix..........: Available
WARNING:root:Received uncompressed content from OpenML for https://api.openml.org/data/v1/download/22103247/pol.arff.
OpenML Classification Task
==========================
Task Type Description: https://www.openml.org/tt/TaskType.SUPERVISED_CLASSIFICATION
Task ID..............: 361062
Task URL.............: https://www.openml.org/t/361062
Estimation Procedure.: crossvalidation
Evaluation Measure...: predictive_accuracy
Target Feature.......: binaryClass
# of Classes.........: 2
Cost Matrix..........: Available
WARNING:root:Received uncompressed content from OpenML for https://api.openml.org/data/v1/download/22103248/house_16H.arff.
OpenML Classification Task
==========================
Task Type Description: https://www.openml.org/tt/TaskType.SUPERVISED_CLASSIFICATION
Task ID..............: 361063
Task URL.............: https://www.openml.org/t/361063
Estimation Procedure.: crossvalidation
Evaluation Measure...: predictive_accuracy
Target Feature.......: binaryClass
# of Classes.........: 2
Cost Matrix..........: Available
WARNING:root:Received uncompressed content from OpenML for https://api.openml.org/data/v1/download/22103250/MagicTelescope.arff.
OpenML Classification Task
==========================
Task Type Description: https://www.openml.org/tt/TaskType.SUPERVISED_CLASSIFICATION
Task ID..............: 361065
Task URL.............: https://www.openml.org/t/361065
Estimation Procedure.: crossvalidation
Evaluation Measure...: predictive_accuracy
Target Feature.......: class
# of Classes.........: 2
Cost Matrix..........: Available
WARNING:root:Received uncompressed content from OpenML for https://api.openml.org/data/v1/download/22103251/bank-marketing.arff.
OpenML Classification Task
==========================
Task Type Description: https://www.openml.org/tt/TaskType.SUPERVISED_CLASSIFICATION
Task ID..............: 361066
Task URL.............: https://www.openml.org/t/361066
Estimation Procedure.: crossvalidation
Evaluation Measure...: predictive_accuracy
Target Feature.......: Class
# of Classes.........: 2
Cost Matrix..........: Available
WARNING:root:Received uncompressed content from OpenML for https://api.openml.org/data/v1/download/22103253/MiniBooNE.arff.
OpenML Classification Task
==========================
Task Type Description: https://www.openml.org/tt/TaskType.SUPERVISED_CLASSIFICATION
Task ID..............: 361068
Task URL.............: https://www.openml.org/t/361068
Estimation Procedure.: crossvalidation
Evaluation Measure...: predictive_accuracy
Target Feature.......: signal
# of Classes.........: 2
Cost Matrix..........: Available
WARNING:root:Received uncompressed content from OpenML for https://api.openml.org/data/v1/download/22103254/Higgs.arff.
OpenML Classification Task
==========================
Task Type Description: https://www.openml.org/tt/TaskType.SUPERVISED_CLASSIFICATION
Task ID..............: 361069
Task URL.............: https://www.openml.org/t/361069
Estimation Procedure.: crossvalidation
Evaluation Measure...: predictive_accuracy
Target Feature.......: target
# of Classes.........: 2
Cost Matrix..........: Available
WARNING:root:Received uncompressed content from OpenML for https://api.openml.org/data/v1/download/22103255/eye_movements.arff.
OpenML Classification Task
==========================
Task Type Description: https://www.openml.org/tt/TaskType.SUPERVISED_CLASSIFICATION
Task ID..............: 361070
Task URL.............: https://www.openml.org/t/361070
Estimation Procedure.: crossvalidation
Evaluation Measure...: predictive_accuracy
Target Feature.......: label
# of Classes.........: 2
Cost Matrix..........: Available
WARNING:root:Received uncompressed content from OpenML for https://api.openml.org/data/v1/download/22111908/Diabetes130US.arff.
OpenML Classification Task
==========================
Task Type Description: https://www.openml.org/tt/TaskType.SUPERVISED_CLASSIFICATION
Task ID..............: 361273
Task URL.............: https://www.openml.org/t/361273
Estimation Procedure.: crossvalidation
Evaluation Measure...: predictive_accuracy
Target Feature.......: readmitted
# of Classes.........: 2
Cost Matrix..........: Available
WARNING:root:Received uncompressed content from OpenML for https://api.openml.org/data/v1/download/22111907/jannis.arff.
OpenML Classification Task
==========================
Task Type Description: https://www.openml.org/tt/TaskType.SUPERVISED_CLASSIFICATION
Task ID..............: 361274
Task URL.............: https://www.openml.org/t/361274
Estimation Procedure.: crossvalidation
Evaluation Measure...: predictive_accuracy
Target Feature.......: class
# of Classes.........: 2
Cost Matrix..........: Available
WARNING:root:Received uncompressed content from OpenML for https://api.openml.org/data/v1/download/22111906/default-of-credit-card-clients.arff.
OpenML Classification Task
==========================
Task Type Description: https://www.openml.org/tt/TaskType.SUPERVISED_CLASSIFICATION
Task ID..............: 361275
Task URL.............: https://www.openml.org/t/361275
Estimation Procedure.: crossvalidation
Evaluation Measure...: predictive_accuracy
Target Feature.......: y
# of Classes.........: 2
Cost Matrix..........: Available
WARNING:root:Received uncompressed content from OpenML for https://api.openml.org/data/v1/download/22111905/Bioresponse.arff.
OpenML Classification Task
==========================
Task Type Description: https://www.openml.org/tt/TaskType.SUPERVISED_CLASSIFICATION
Task ID..............: 361276
Task URL.............: https://www.openml.org/t/361276
Estimation Procedure.: crossvalidation
Evaluation Measure...: predictive_accuracy
Target Feature.......: target
# of Classes.........: 2
Cost Matrix..........: Available
WARNING:root:Received uncompressed content from OpenML for https://api.openml.org/data/v1/download/22111914/california.arff.
OpenML Classification Task
==========================
Task Type Description: https://www.openml.org/tt/TaskType.SUPERVISED_CLASSIFICATION
Task ID..............: 361277
Task URL.............: https://www.openml.org/t/361277
Estimation Procedure.: crossvalidation
Evaluation Measure...: predictive_accuracy
Target Feature.......: price_above_median
# of Classes.........: 2
Cost Matrix..........: Available
WARNING:root:Received uncompressed content from OpenML for https://api.openml.org/data/v1/download/22111912/heloc.arff.
OpenML Classification Task
==========================
Task Type Description: https://www.openml.org/tt/TaskType.SUPERVISED_CLASSIFICATION
Task ID..............: 361278
Task URL.............: https://www.openml.org/t/361278
Estimation Procedure.: crossvalidation
Evaluation Measure...: predictive_accuracy
Target Feature.......: RiskPerformance
# of Classes.........: 2
Cost Matrix..........: Available

```

In [8]:
import openml
openml.config.apikey = 'e6d1ecc68afe6fbcd296c034335dd888'  # set the OpenML Api Key

# # SUITE_ID = 336 # Regression on numerical features
# SUITE_ID = 337 # Classification on numerical features
# #SUITE_ID = 335 # Regression on numerical and categorical features
# #SUITE_ID = 334 # Classification on numerical and categorical features
# benchmark_suite = openml.study.get_suite(SUITE_ID)  # obtain the benchmark suite
# for task_id in benchmark_suite.tasks:  # iterate over all tasks
#     task = openml.tasks.get_task(task_id)  # download the OpenML task
#     dataset = task.get_dataset()
#     X, y, categorical_indicator, attribute_names = dataset.get_data(
#         dataset_format="dataframe", target=dataset.default_target_attribute
#     )

dataset = openml.tasks.get_task(361277).get_dataset() # download the OpenML dataset
print(task)

classification


In [9]:
X, y, categorical_indicator, attribute_names = dataset.get_data(
    dataset_format="array", target=dataset.default_target_attribute
)
print('converting types')
X = X.astype(np.float64)
y = y.astype(np.float64)

# print('normalizing X')
# X_mean = X.mean(0, keepdims=True)
# X_std = X.std(0, keepdims=True)
# X -= X_mean
# X /= X_std
# use QuantileTransformer to normalize X
X = QuantileTransformer(
    output_distribution="normal", random_state=42
).fit_transform(X)

converting types


In [10]:
X.shape, y.shape

((20634, 8), (20634,))

In [11]:
X[:10]

array([[-1.00727874, -0.16128127, -0.6021534 , -1.87914254, -1.75410366,
        -1.10595274,  2.08384147, -1.02088842],
       [-0.29897377,  0.19186514, -0.51193781, -1.04377977,  1.86777133,
         1.84001628, -1.79237402,  1.68446368],
       [-1.36291931,  0.84807465, -0.45188429,  0.92591266, -0.38572587,
         0.96870844,  0.72824036, -1.08645605],
       [-1.79866258,  0.65648594, -0.85155273,  0.72007497,  0.61805886,
         1.01438148, -0.52641687,  0.28482819],
       [-1.27755486, -1.22594275, -1.61544799, -1.0252176 , -1.79066564,
         1.73350705, -0.57311539,  0.47100434],
       [ 0.21877307,  1.44610359, -0.25758873, -1.1251175 , -1.39120206,
        -0.39574431,  0.78332986, -1.10013967],
       [-1.64354445,  0.33883407, -2.40598894, -0.44484303,  0.2239158 ,
         0.31261037, -0.38032564,  0.26788377],
       [-1.71602647,  0.7901684 , -1.43612441,  0.81763597,  0.38810618,
         1.34493352, -0.59843525,  0.26788377],
       [-0.51206059,  0.43900121

In [12]:
y[:10]

array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0.])

In [13]:
X_train, X_test, y_train, y_test = train_test_split(X, y, train_size=(k_fold-1)/k_fold, 
                                                    shuffle=True, random_state=42)

In [14]:
print(X_train.shape, y_train.shape)
print(X_test.shape, y_test.shape)

(16507, 8) (16507,)
(4127, 8) (4127,)


In [15]:
histogram(np.linalg.norm(X_train, axis=1, ord=2))

In [16]:
heur_sigma, distances = get_sigma_heuristic(X_train, sample_size=200, return_dist=True)
print('heuristic bandwidth:', heur_sigma)

heuristic bandwidth: 3.953302764874331


In [17]:
histogram(sample(distances, 10000))

In [18]:
if ydim == 1:
    fig = histogram(y_train)
else:
    fig = histogram(np.argmax(y_train, axis=-1))
fig.show()

### Standard Thinning (ST)

In [19]:
%%time
sd_coreset = sd_thin(X_train, m=m)
print('sd coreset:', len(sd_coreset))
X_train_sd_thin, y_train_sd_thin = X_train[sd_coreset], y_train[sd_coreset]

sd coreset: 128
CPU times: user 386 µs, sys: 126 µs, total: 512 µs
Wall time: 408 µs


### Kernel Thinning (KT)

In [20]:
from functools import partial

# KERNEL THINNING

# Define kernel params
d = X_train.shape[-1]
var_k = sigma**2
params_k_swap = {"name": kernel, "var": var_k, "d": int(d)}
params_k_split = {"name": kernel, "var": var_k, "d": int(d)}

split_kernel = partial(kernel_eval, params_k=params_k_split)
swap_kernel = partial(kernel_eval, params_k=params_k_swap)

regression_split_kernel = to_regression_kernel(split_kernel, ydim=ydim)
regression_swap_kernel = to_regression_kernel(swap_kernel, ydim=ydim)

In [21]:
Xy_train = get_Xy(X_train, y_train)
print(Xy_train.shape)


(16507, 9)


In [22]:
# %lprun -f kt_thin3 kt_coreset = kt_thin3(X_train, split_kernel, swap_kernel, m=m)

In [23]:
# from goodpoints.compress import compress_gsn_kt
# X_intermediate = compress_gsn_kt(X_train)

In [24]:
# from goodpoints import compress
# %lprun -f compress.compresspp ktr_coreset = kt_thin2(Xy_train, regression_split_kernel, regression_swap_kernel, m=m, store_K=True)

| n | 5,000 | 20,000 |
| -------- | -------- | -------- |
| store_K=True | 7.9s | 46.9s |
| store_K=False | 20.8s | 1m59s |

In [25]:
# X_train_ktr_thin, y_train_ktr_thin = X_train[ktr_coreset], y_train[ktr_coreset]

In [26]:
# X_train_ktr_thin.shape

In [27]:
# print('n:', len(Xy_train))
# log2n = int(np.log2(len(Xy_train)))
# log4n = int(np.log2(len(Xy_train)) / 2)
# print('log2n:', log2n)
# print('log4n:', log4n) 

# print('2^log2n:', 2**log2n)
# print('4^log4n:', 4**log4n)

# for i in range(log2n // 2 + 1):
#     with TicToc():
#         print(i, kt_thin2(Xy_train, regression_split_kernel, regression_swap_kernel, m=i).shape[0])
#         print(i, sd_thin(X_train, m=i).shape[0])

## KRR (Full)

In [72]:
krr_full = get_estimator(
    'regression',
    'full', 
    alpha=alpha, 
    kernel=kernel, 
    sigma=sigma, 
    postprocess=None, # no postprocessing so that we can compute the MSE
)

In [73]:
krr_full

KernelRidgeRegressor(alpha=0.001, sigma=10)

In [74]:
%%time
K_full = krr_full.fit(X_train, y_train)

CPU times: user 36.6 s, sys: 8.37 s, total: 45 s
Wall time: 13.1 s


In [75]:
histogram(sample(K_full.flatten(), n=10000))

In [76]:
pred_full = krr_full.predict(X_test)
train_pred_full = krr_full.predict(X_train)

In [77]:
fig = make_subplots(rows=2, cols=1, subplot_titles=['train', 'test'])

fig.add_trace(go.Histogram(x=train_pred_full.flatten(), name='train', opacity=0.5), row=1, col=1)
fig.add_trace(go.Histogram(x=y_train.flatten(), name='ground truth', opacity=0.5, legendgroup=1), row=1, col=1)

fig.add_trace(go.Histogram(x=pred_full.flatten(), name='test', opacity=0.5), row=2, col=1)
fig.add_trace(go.Histogram(x=y_test.flatten(), name='ground truth', opacity=0.5, legendgroup=1), row=2, col=1)
fig.show()

In [78]:
print('Train acc:', classification_accuracy(y_train, train_pred_full))
print('acc:', classification_accuracy(y_test, pred_full))
print()
print('Train MSE:', mean_squared_error(y_train, train_pred_full))
print('MSE:', mean_squared_error(y_test, pred_full))

Train acc: 1.0
acc: 0.8672158953234795

Train MSE: 3.3518612044405446e-05
MSE: 0.09684279114419977


In [35]:
histogram(krr_full.sol_)

In [36]:
len(krr_full.sol_)

16507

## KRR Low Rank

In [79]:
krr_lowrank = get_estimator(
    'regression',
    'lowrank', 
    alpha=alpha, 
    kernel=kernel, 
    sigma=10, 
    postprocess=None, # no postprocessing so that we can compute the MSE
    rfm_iters=10,
)

In [80]:
%%time
krr_lowrank.fit(X_train, y_train, val_data=(X_test,y_test), rank=8)

learning feature matrix...
Round 0, Test MSE: 0.0968
Using batch size of 4032


  0%|          | 0/5 [00:00<?, ?it/s]

Round 1, Test MSE: 0.0863
Using batch size of 4032


  0%|          | 0/5 [00:00<?, ?it/s]

Round 2, Test MSE: 0.0800
Using batch size of 4032


...

  0%|          | 0/5 [00:00<?, ?it/s]

Round 9, Test MSE: 0.0655
Using batch size of 4032


  0%|          | 0/5 [00:00<?, ?it/s]

Final MSE: 0.0649
(16507, 8)
CPU times: user 8min 5s, sys: 1min 7s, total: 9min 13s
Wall time: 1min 51s


array([[1.        , 0.75510585, 0.65491313, ..., 0.61502286, 0.72244637,
        0.51233213],
       [0.75510585, 1.        , 0.64668025, ..., 0.5555907 , 0.73578642,
        0.52924776],
       [0.65491313, 0.64668025, 1.        , ..., 0.81324205, 0.86252728,
        0.75219116],
       ...,
       [0.61502286, 0.5555907 , 0.81324205, ..., 1.        , 0.74472388,
        0.73011408],
       [0.72244637, 0.73578642, 0.86252728, ..., 0.74472388, 1.        ,
        0.69995468],
       [0.51233213, 0.52924776, 0.75219116, ..., 0.73011408, 0.69995468,
        1.        ]])

In [81]:
pred_lowrank = krr_lowrank.predict(X_test)
train_pred_lowrank = krr_lowrank.predict(X_train)

In [71]:
print('Train acc:', classification_accuracy(y_train, train_pred_lowrank))
print('acc:', classification_accuracy(y_test, pred_lowrank))
print()
print('Train MSE:', mean_squared_error(y_train, train_pred_lowrank))
print('MSE:', mean_squared_error(y_test, pred_lowrank))

Train acc: 1.0
acc: 0.9159195541555609

Train MSE: 0.0004264198494769262
MSE: 0.06487066322063148


## KRR + ST

In [37]:
krr_sd_thin = get_estimator(
    'regression', 
    'st', 
    alpha=alpha, # / np.power(len(X_train), 1/4), 
    kernel=kernel, 
    sigma=sigma, 
    m=m, 
    postprocess=None
)

In [38]:
%%time
krr_sd_thin.fit(X_train, y_train)

CPU times: user 23.9 ms, sys: 9.76 ms, total: 33.7 ms
Wall time: 5.57 ms


In [39]:
krr_sd_thin.X_fit_.shape

(128, 8)

In [40]:
%%time
pred_sd = krr_sd_thin.predict(X_test)
train_pred_sd = krr_sd_thin.predict(X_train)


CPU times: user 214 ms, sys: 104 ms, total: 318 ms
Wall time: 39 ms


In [41]:
print('Train acc:', classification_accuracy(y_train, train_pred_sd))
print('acc:', classification_accuracy(y_test, pred_sd))
print()
print('train MSE:', mean_squared_error(y_train, krr_sd_thin.predict(X_train)))
print('MSE:', mean_squared_error(y_test, pred_sd))

Train acc: 0.7747622220875992
acc: 0.7799854615943785

train MSE: 0.15644560579906805
MSE: 0.15855413243625752


## KRR + KT

In [42]:
krr_kt_thin = get_estimator(
    'regression',
    'kt', 
    kernel=kernel, 
    alpha=alpha, # / np.power(len(X_train), 1/4), 
    sigma=sigma, 
    m=m, 
    postprocess=None,
    ydim=ydim,
)

In [43]:
%%time
krr_kt_thin.fit(X_train, y_train)

# To run line profiler, uncomment the next line
# %lprun -f krr_kt_thin.fit krr_kt_thin.fit(X_train, y_train)

CPU times: user 1.24 s, sys: 614 ms, total: 1.86 s
Wall time: 758 ms


In [44]:
krr_kt_thin.X_fit_.shape

(128, 8)

In [45]:
%%time
pred_kt = krr_kt_thin.predict(X_test)
train_pred_kt = krr_kt_thin.predict(X_train)


CPU times: user 357 ms, sys: 61.3 ms, total: 418 ms
Wall time: 51.2 ms


In [46]:
print('Train acc:', classification_accuracy(y_train, train_pred_kt))
print('acc:', classification_accuracy(y_test, pred_kt))
print()
print('train MSE:', mean_squared_error(y_train, krr_kt_thin.predict(X_train)))
print('MSE:', mean_squared_error(y_test, pred_kt))

Train acc: 0.8222572242079118
acc: 0.8286891204264599

train MSE: 0.12920007086130178
MSE: 0.12641631722663302


## RFM

Note: changing the bandwidth for RFM doesn't make a big difference, since increasing bandwidth will lead to greater weight values. However, there is a big difference in terms of numerical stability. Therefore, it's better to use the default bandwidth $L=10$.

In [47]:
rfm = get_estimator(
    'regression', 
    'rfm', 
    alpha=alpha, 
    kernel=kernel, 
    sigma=sigma,
    iters=rfm_iters,
    ydim=ydim,
)

In [48]:
rfm

RFMRegressor(alpha=0.001, kernel='laplace', sigma=10)

In [49]:
Ms, mses, preds = rfm.fit(
    X_train, y_train, 
    val_data=(X_test, y_test),
)

Round 0, Test MSE: 0.0968
Using batch size of 4032


  0%|          | 0/5 [00:00<?, ?it/s]

Final MSE: 0.0863


In [50]:
# plot correlation matrices Ms as subplots
fig = make_subplots(rows=1, cols=len(Ms), subplot_titles=[f'iter {i}' for i in range(len(Ms))])
for i, M in enumerate(Ms):
    # add image
    fig.add_trace(go.Heatmap(z=M, showlegend=False), row=1, col=i+1)
    fig.update_layout(height=400, width=1000, title_text="Feature matrix per iteration")
fig.show()

In [51]:
histogram(rfm._model.weights)

In [52]:
%%time
pred_rfm = rfm.predict(X_test)
train_pred_rfm = rfm.predict(X_train)

CPU times: user 2.5 s, sys: 282 ms, total: 2.78 s
Wall time: 688 ms


In [53]:
pred_rfm

array([[0.01043632],
       [0.2335847 ],
       [0.69918083],
       ...,
       [0.12426341],
       [0.55580736],
       [0.61349971]])

In [54]:
print('Train acc:', classification_accuracy(y_train, train_pred_rfm))
print('acc:', classification_accuracy(y_test, pred_rfm))
print()
print('train MSE:', mean_squared_error(y_train, train_pred_rfm))
print('MSE:', mean_squared_error(y_test, pred_rfm))

Train acc: 1.0
acc: 0.8824812212260722

train MSE: 0.00041809638143160084
MSE: 0.08627375696216454


## KRR + KT + Feature Learning

In [55]:
krr_kf_thin = get_estimator(
    'regression',
    'kf', 
    kernel=kernel, 
    alpha=alpha, # / np.power(len(X_train), 1/4), 
    sigma=10, 
    m=m, 
    postprocess=None,
    ydim=ydim,
    rfm_iters=10,
    # rank=8
)

In [56]:
krr_kf_thin

KernelRidgeKTFeatureRegressor(alpha=0.001, rfm_iters=10)

In [57]:
%%time
# krr_kf_thin.rank = 8
K = krr_kf_thin.fit(X_train, y_train, val_data=(X_test, y_test))

learning feature matrix...


Round 0, Test MSE: 0.0968
Using batch size of 4032


  0%|          | 0/5 [00:00<?, ?it/s]

Round 1, Test MSE: 0.0863
Using batch size of 4032


  0%|          | 0/5 [00:00<?, ?it/s]

...

  0%|          | 0/5 [00:00<?, ?it/s]

Round 9, Test MSE: 0.0655
Using batch size of 4032


  0%|          | 0/5 [00:00<?, ?it/s]

Final MSE: 0.0649


CPU times: user 13min 9s, sys: 6min 44s, total: 19min 53s
Wall time: 1min 31s


In [58]:
%%time
pred_kf = krr_kf_thin.predict(X_test)
train_pred_kf = krr_kf_thin.predict(X_train)

CPU times: user 304 ms, sys: 20.1 ms, total: 324 ms
Wall time: 22 ms


In [59]:
print('Train acc:', classification_accuracy(y_train, train_pred_kf))
print('acc:', classification_accuracy(y_test, pred_kf))
print()
print('train MSE:', mean_squared_error(y_train, train_pred_kf))
print('MSE:', mean_squared_error(y_test, pred_kf))

Train acc: 0.7229054340582783
acc: 0.7167433971407803

train MSE: 1.6271790119956768
MSE: 1.6486647551733542


In [60]:
%%time
# krr_kf_thin.rank = 8
K = krr_kf_thin.fit(X_train, y_train, val_data=(X_test, y_test), rank=2)
pred_kf = krr_kf_thin.predict(X_test)
train_pred_kf = krr_kf_thin.predict(X_train)

(16507, 2)


CPU times: user 4.38 s, sys: 71.6 ms, total: 4.45 s
Wall time: 907 ms


In [61]:
print('Train acc:', classification_accuracy(y_train, train_pred_kf))
print('acc:', classification_accuracy(y_test, pred_kf))
print()
print('train MSE:', mean_squared_error(y_train, train_pred_kf))
print('MSE:', mean_squared_error(y_test, pred_kf))

Train acc: 0.6617798509723147
acc: 0.6658589774654713

train MSE: 1.7674295210078033
MSE: 1.6717894913556304


In [62]:
fig = go.Figure(data=[go.Heatmap(z=krr_kf_thin.M)])
fig.update_layout(height=400, width=400, title_text="Feature matrix")
fig.show()

In [63]:
np.linalg.svd(krr_kf_thin.M)[1]

array([7.20165732e+00, 4.29762625e+00, 1.41615125e-01, 2.02253172e-02,
       1.22930320e-02, 6.07160170e-03, 9.22725611e-04, 1.46009243e-04])

In [64]:
U, S, V = np.linalg.svd(krr_kf_thin.M)
W = np.diag(np.sqrt(S)) @ V
print(np.isclose(krr_kf_thin.M, W.T @ W))

[[ True  True  True  True  True  True  True  True]
 [ True  True  True  True  True  True  True  True]
 [ True  True  True  True  True  True  True  True]
 [ True  True  True  True  True  True  True  True]
 [ True  True  True  True  True  True  True  True]
 [ True  True  True  True  True  True  True  True]
 [ True  True  True  True  True  True  True  True]
 [ True  True  True  True  True  True  True  True]]


In [65]:
from goodpoints.krr.util_k_mmd import laplacian, laplacian_M

In [66]:
laplacian(X_test, X_test, sigma)

array([[1.        , 0.57134342, 0.65761896, ..., 0.62982597, 0.6431303 ,
        0.6449978 ],
       [0.57134342, 1.        , 0.68731841, ..., 0.70634685, 0.71904356,
        0.64224553],
       [0.65761896, 0.68731841, 1.        , ..., 0.64361118, 0.6827845 ,
        0.77619631],
       ...,
       [0.62982597, 0.70634685, 0.64361118, ..., 1.        , 0.86351658,
        0.57323381],
       [0.6431303 , 0.71904356, 0.6827845 , ..., 0.86351658, 1.        ,
        0.6028259 ],
       [0.6449978 , 0.64224553, 0.77619631, ..., 0.57323381, 0.6028259 ,
        0.99999999]])

In [67]:
laplacian(X_test @ W.T, X_test @ W.T, sigma)

array([[1.        , 0.82770122, 0.58661727, ..., 0.80951522, 0.73720113,
        0.60595797],
       [0.82770122, 1.        , 0.67377517, ..., 0.95626749, 0.85388203,
        0.6926639 ],
       [0.58661727, 0.67377517, 1.        , ..., 0.67007667, 0.75887219,
        0.95945539],
       ...,
       [0.80951522, 0.95626749, 0.67007667, ..., 1.        , 0.86158484,
        0.68844649],
       [0.73720113, 0.85388203, 0.75887219, ..., 0.86158484, 1.        ,
        0.78191943],
       [0.60595797, 0.6926639 , 0.95945539, ..., 0.68844649, 0.78191943,
        1.        ]])

In [68]:
laplacian_M(X_test, X_test, krr_kf_thin.M, sigma)

array([[1.        , 0.82770122, 0.58661727, ..., 0.80951522, 0.73720113,
        0.60595797],
       [0.82770122, 1.        , 0.67377517, ..., 0.95626749, 0.85388203,
        0.6926639 ],
       [0.58661727, 0.67377517, 1.        , ..., 0.67007667, 0.75887219,
        0.95945539],
       ...,
       [0.80951522, 0.95626749, 0.67007667, ..., 1.        , 0.86158484,
        0.68844649],
       [0.73720113, 0.85388203, 0.75887219, ..., 0.86158484, 1.        ,
        0.78191943],
       [0.60595797, 0.6926639 , 0.95945539, ..., 0.68844649, 0.78191943,
        1.        ]])

In [69]:
# np.isclose(laplacian(X_test @ W.T, X_test @ W.T, sigma), laplacian_M(X_test, X_test, krr_kf_thin.M, sigma), rtol=0, atol=1e-12).all()
np.median(np.abs(laplacian(X_test @ W.T, X_test @ W.T, sigma) -laplacian_M(X_test, X_test, krr_kf_thin.M, sigma)).flatten())

0.0

In [70]:
krr_kf_thin.W.shape

(2, 8)

In [71]:
krr_kf_thin.X_fit_.shape

(128, 8)

In [72]:
K.shape

(128, 128)

In [73]:
histogram(K.flatten())

In [74]:
histogram(krr_kf_thin.sol_)

## RFM-Thin

In [75]:
rfm_thin = get_estimator(
    'regression', 
    'rfm', 
    alpha=alpha, 
    kernel=kernel, 
    sigma=sigma,
    iters=rfm_iters,
    ydim=ydim,
    use_kt = True,
)

In [76]:
Ms, mses, preds = rfm_thin.fit(
    X_train, y_train, 
    val_data=(X_test, y_test),
)

Using kernel thinning to select centers...


Round 0, Test MSE: 0.1324
Using batch size of 4032


  0%|          | 0/5 [00:00<?, ?it/s]

Using kernel thinning to select centers...


Final MSE: 0.1261


In [77]:
%%time
pred_rfm_thin = rfm_thin.predict(X_test)
train_pred_rfm_thin = rfm_thin.predict(X_train)

CPU times: user 33.9 ms, sys: 13 ms, total: 46.9 ms
Wall time: 3.38 ms


In [78]:
print('Train acc:', classification_accuracy(y_train, train_pred_rfm_thin))
print('acc:', classification_accuracy(y_test, pred_rfm_thin))
print()
print('train MSE:', mean_squared_error(y_train, train_pred_rfm_thin))
print('MSE:', mean_squared_error(y_test, pred_rfm_thin))

Train acc: 0.8279517780335616
acc: 0.8371698570390114

train MSE: 0.12576389681716926
MSE: 0.12613523850627814


## FALKON

In [79]:
krr_falkon = get_estimator(
    task,
    'falkon',
    kernel=kernel,
    sigma=sigma,
    alpha=alpha,
    m=m,
    postprocess=postprocess,
)

[KeOps] Warning : Cuda libraries were not detected on the system or could not be loaded ; using cpu only mode


In [80]:
%%time
if krr_falkon:
    krr_falkon.fit(X_train, y_train)

CPU times: user 4.48 s, sys: 192 ms, total: 4.67 s
Wall time: 442 ms


In [81]:
%%time
if krr_falkon:
    pred_falkon = krr_falkon.predict(X_test)
    train_pred_falkon = krr_falkon.predict(X_train)

    print('Train acc:', classification_accuracy(y_train, train_pred_falkon))
    print('acc:', classification_accuracy(y_test, pred_falkon))
    print()
    print('train MSE:', mean_squared_error(y_train, train_pred_falkon))
    print('MSE:', mean_squared_error(y_test, pred_falkon))

Train acc: 0.8425516447567698
acc: 0.843712139568694

train MSE: 0.15744835524323014
MSE: 0.15628786043130605
CPU times: user 101 ms, sys: 0 ns, total: 101 ms
Wall time: 6.33 ms


## FALKON + KT

In [82]:
# krr_falkon_kt = get_estimator(
#     task,
#     'falkon+kt',
#     kernel=kernel,
#     sigma=sigma,
#     alpha=alpha,
#     m=m,
#     postprocess=postprocess,
#     ydim=ydim,
# )

In [83]:
# %lprun -f krr_falkon_kt.fit krr_falkon_kt.fit(X_train, y_train)

In [84]:
# %%time
# if krr_falkon_kt:
#     pred_falkon_kt = krr_falkon_kt.predict(X_test)
#     print('Score:', accuracy_score(y_test, pred_falkon_kt))
#     print('RMSE:', np.sqrt(mean_squared_error(y_test, pred_falkon_kt)))

## Run experiment

We now run a full grid search with cross validation across different-size datasets.

Reference: https://scikit-learn.org/stable/auto_examples/ensemble/plot_forest_hist_grad_boosting_comparison.html#sphx-glr-auto-examples-ensemble-plot-forest-hist-grad-boosting-comparison-py

In [85]:
from sklearn.model_selection import GridSearchCV, KFold

In [86]:
# NOTE: these will only be applied if `use_cross_validation` is True
# Default param grid to search for each model
default_param_grid = {
    "sigma" :   [10,], 
    "alpha" :   [10, 1, 1e-1, 1e-2, 1e-3, 1e-4],
}
falkon_param_grid = {
    "sigma" :   [10,],
    "alpha" :   [1e-2, 1e-3, 1e-4,1e-5,1e-6, 0], # Falkon requires smaller alpha
}
# falkon_param_grid = default_param_grid

# rfm_param_grid = {
#     "sigma" :   [10,], 
#     "alpha" :   [1e-3,1e-4,1e-5],
#     # "iters" :   [1,2,3],
# }
rfm_param_grid = default_param_grid

In [87]:
# The different values will correspond to different columns in the final plots
varying_variable = 'kernel'
varying_variable_values = ['gauss', 'laplace',]
datasets = ['housing',]

In [88]:
# Model constructors and data size for each model
# We allow for different data sizes to avoid running Full KR on large datasets
model_configs = {
    'full' : {
        'dataset' : datasets,
        'kwargs': {
            'postprocess' : postprocess
        },
        'param_grid' : default_param_grid
    },
}

# for m in [None,]:
model_configs[f'st'] = {
    'dataset' : datasets,
    'kwargs' : {
        'm' : m,
        'postprocess' : postprocess
    },
    'param_grid' : default_param_grid
}

model_configs[f'kt'] = {
    'dataset' : datasets,
    'kwargs' : {
        'm' : m,
        'postprocess' : postprocess,
        'ydim' : ydim,
    },
    'param_grid' : default_param_grid
}

model_configs[f'falkon'] = {
    'dataset' : datasets,
    'kwargs' : {
        'm' : m,
        'postprocess' : postprocess,
    },
    'param_grid' : falkon_param_grid
}

# model_configs[f'falkon+kt_{m}'] = {
#     'dataset' : datasets,
#     'kwargs' : {
#         'm' : m,
#         'postprocess' : postprocess,
#         'ydim' : ydim,
#     },
#     'param_grid' : falkon_param_grid
# }
model_configs[f'rfm'] = {
    'dataset' : datasets,
    'kwargs' : {
        'iters' : rfm_iters,
        'postprocess' : postprocess,
    },
    'param_grid' : rfm_param_grid
}

model_configs[f'kf'] = {
    'dataset' : datasets,
    'kwargs' : {
        'm' : m,
        'postprocess' : postprocess,
        'ydim' : ydim,
        'rfm_iters' : rfm_iters,
    },
    'param_grid' : rfm_param_grid
}

model_configs[f'rfm-thin'] = {
    'dataset' : datasets,
    'kwargs' : {
        'iters' : rfm_iters,
        'use_kt' : True,
        'postprocess' : postprocess,
    },
    'param_grid' : rfm_param_grid
}

In [89]:
model_configs

{'full': {'dataset': ['housing'],
  'kwargs': {'postprocess': 'threshold'},
  'param_grid': {'sigma': [10], 'alpha': [10, 1, 0.1, 0.01, 0.001, 0.0001]}},
 'st': {'dataset': ['housing'],
  'kwargs': {'m': None, 'postprocess': 'threshold'},
  'param_grid': {'sigma': [10], 'alpha': [10, 1, 0.1, 0.01, 0.001, 0.0001]}},
 'kt': {'dataset': ['housing'],
  'kwargs': {'m': None, 'postprocess': 'threshold', 'ydim': 1},
  'param_grid': {'sigma': [10], 'alpha': [10, 1, 0.1, 0.01, 0.001, 0.0001]}},
 'falkon': {'dataset': ['housing'],
  'kwargs': {'m': None, 'postprocess': 'threshold'},
  'param_grid': {'sigma': [10],
   'alpha': [0.01, 0.001, 0.0001, 1e-05, 1e-06, 0]}},
 'rfm': {'dataset': ['housing'],
  'kwargs': {'iters': 1, 'postprocess': 'threshold'},
  'param_grid': {'sigma': [10], 'alpha': [10, 1, 0.1, 0.01, 0.001, 0.0001]}},
 'kf': {'dataset': ['housing'],
  'kwargs': {'m': None, 'postprocess': 'threshold', 'ydim': 1, 'rfm_iters': 1},
  'param_grid': {'sigma': [10], 'alpha': [10, 1, 0.1, 0.0

In [90]:
use_cross_validation

True

In [91]:
# Run experiment (depending on experiment_type)

results = []

count = 0
for name, config in model_configs.items():
    for dataset in config['dataset']:

        for v in varying_variable_values:
            kwargs = deepcopy(config['kwargs'])
            kwargs[varying_variable] = v
            model_name = f"{name}_{v}"
            # NOTE: full and rfm are deterministic, so we only need to run them once
            trials = (1 if name in ['full', 'rfm'] else n_repeats)

            # STEP 1: Get data
            # use X_train, y_train, X_test, y_test from above
            
            if 'kernel' not in kwargs:
                kwargs['kernel'] = kernel

            model = get_estimator(task, name=name, **kwargs)
            if model is None: continue
            print(f'i={count+1}: dataset={dataset}, model={model}')

            # STEP 2: Get optimal parameters through grid search
            # NOTE: we want to get rid of randomness in the Kernel Thinning (or Standard Thinning) routine
            # so we do k-fold cross validation `trials` times using the *same* split.
            # This is different from sklearn's repeated k-fold implementation which uses a 
            # different random split each time.            

            if use_cross_validation:
                split = list(KFold(n_splits=k_fold).split(X_train)) * trials
                grid_search = GridSearchCV(
                    estimator=model,
                    param_grid=config['param_grid'],
                    return_train_score=True,
                    cv=split,
                    scoring=refit,
                    refit=False,
                    n_jobs=n_jobs,
                ).fit(X_train, y_train)
                # get validation scores
                cv_results = pd.DataFrame(grid_search.cv_results_)
                val_scores = []
                for i in range(trials):
                    # compute classification error from accuracy
                    val_scores.append( 1-cv_results.iloc[grid_search.best_index_][f'split{i}_test_score'] )
            
                # get optimal parameters
                best_params = grid_search.best_params_
            
            else:
                # Dummy values (these won't be displayed in the plots)
                val_scores = [np.nan,] * trials
                
                best_params = {
                    'sigma' : sigma,
                    'alpha' : alpha, # * (len(X_train)**(1/4) if name in ['st', 'kt'] else 1),
                }
            print(f"best params: {best_params}")
            best_model = get_estimator(task, name=name, 
                                       sigma=best_params['sigma'],
                                       alpha=best_params['alpha'],
                                       **kwargs)
            print(best_model)

            # STEP: Estimate test score
            train_scores = []
            test_scores = []
            for _ in range(trials):
                best_model.fit(X_train, y_train)

                # compute train score
                train_pred = best_model.predict(X_train).squeeze()
                # compute test score
                test_pred = best_model.predict(X_test).squeeze()

                train_score = 1- classification_accuracy(y_train, train_pred)
                test_score = 1- classification_accuracy(y_test, test_pred)
                
                train_scores.append( train_score )
                test_scores.append( test_score )

            results.append({
                "dataset": dataset, 
                "model": model_name, 
                "cv_results": pd.DataFrame(grid_search.cv_results_) if use_cross_validation else None,
                "best_index_" : grid_search.best_index_ if use_cross_validation else 0,
                "best_params_" : best_params,
                "val_scores" : val_scores,
                "train_scores" : train_scores,
                "test_scores" : test_scores,
            })

            count += 1

i=1: dataset=housing, model=KernelRidgeClassifier(kernel='gauss', postprocess='threshold')


best params: {'alpha': 0.0001, 'sigma': 10}
KernelRidgeClassifier(alpha=0.0001, kernel='gauss', postprocess='threshold',
                      sigma=10)


i=2: dataset=housing, model=KernelRidgeClassifier(postprocess='threshold')


best params: {'alpha': 0.1, 'sigma': 10}
KernelRidgeClassifier(alpha=0.1, postprocess='threshold', sigma=10)


i=3: dataset=housing, model=KernelRidgeSTClassifier(kernel='gauss', postprocess='threshold')


...

Final MSE: 0.1217
Using kernel thinning to select centers...


Round 0, Test MSE: 0.1273
Using batch size of 4032


  0%|          | 0/5 [00:00<?, ?it/s]

Using kernel thinning to select centers...


Final MSE: 0.1194


In [92]:
results

[{'dataset': 'housing',
  'model': 'full_gauss',
  'cv_results':    mean_fit_time  std_fit_time  mean_score_time  std_score_time param_alpha  \
  0      23.756161      0.076045         0.648197        0.014791          10   
  1      23.509588      0.380780         0.618198        0.037805           1   
  2      31.875929     10.233112         0.790695        0.249132         0.1   
  3      23.088130      0.457964         0.584016        0.042984        0.01   
  4      23.562449      0.058162         0.637486        0.006919       0.001   
  5      23.662116      0.037760         0.621024        0.023570      0.0001   
  
    param_sigma                          params  split0_test_score  \
  0          10      {'alpha': 10, 'sigma': 10}           0.840097   
  1          10       {'alpha': 1, 'sigma': 10}           0.852211   
  2          10     {'alpha': 0.1, 'sigma': 10}           0.860085   
  3          10    {'alpha': 0.01, 'sigma': 10}           0.863719   
  4          10  

In [93]:
# Save results with pickle
if save:
    import pickle
    filename = dataset + ('_cv' if use_cross_validation else '') # '_'.join(['toy', housing])
    pickle_file = filename + '.p'
    print(pickle_file)

    with open(pickle_file, 'wb') as f:
        pickle.dump(results, f)

## Plot Results

In [94]:
import plotly.colors as colors
import seaborn as sns

from functools import reduce
from operator import concat

### Varying variable (e.g., kernel choice)

In [95]:
def plot_results(varying_variable, varying_variable_values, scale='linear'):
    # row_subplot_titles = ["Test score vs n"], #, "Test Neg-MSE vs n"] #, "Train time vs n", "Predict time vs n"]
    row_subplot_titles = ["Test Score", "Val Score", "Train Score"]

    fig = make_subplots(
        rows=len(row_subplot_titles),
        cols=len(varying_variable_values),
        shared_yaxes=True,
        subplot_titles=reduce(concat, [[f'{varying_variable}={v}' for v in varying_variable_values] for _ in row_subplot_titles]),
        vertical_spacing=0.1,
    )
    model_names = [model_name.split('_')[0] for model_name in model_configs.keys()]
    colors_list = colors.qualitative.Plotly * (
        len(model_names) // len(colors.qualitative.Plotly) + 1
    )
    colors_used = set()

    def plot_vs_n(print_name, attr_name, vvv, r, c, is_better='higher', scale='log2'):
        """
        Args:
        - vvv: varying variable value
        """
        
        for result in results:
            model_name = result["model"]
            name_components = model_name.split('_') # E.g., Kernel-Thin_rbf -> Kernel-Thin, rbf
            if len(name_components) == 2:
                model_name_prefix, vv_name = name_components
                m = '0'
            else:
                model_name_prefix, m, vv_name = name_components        
            best_params = result["best_params_"]

            if vv_name != vvv:
                continue

            color = colors_list[model_names.index(model_name_prefix)]

            if scale == 'log2':
                y = np.log2(np.abs(result[attr_name]))
            elif scale == 'linear':
                y = np.abs(result[attr_name])

            trace = go.Box(
                x=[result['dataset']]*len(result[attr_name]),
                y=y,
                name=model_name_prefix,
                # opacity=0.5,
                legendgroup=model_name_prefix,
                line_color=color,
                offsetgroup=model_name_prefix,
                showlegend=color not in colors_used,
                boxmean=True,
            )

            fig.add_trace(trace, row=r, col=c)
            colors_used.add(color)

        if c == 1: fig.update_yaxes(title_text=f"{scale}({print_name}) - {is_better} is better", row=r, col=c)
        fig.update_xaxes(title_text="dataset", row=r, col=c)
        fig.update_layout(boxmode='group')

    def plot_test_score_vs_n(vvv, r, c, scale):
        plot_vs_n(f"Test MSE", "test_scores", vvv, r, c, is_better='lower', scale=scale)

    def plot_val_score_vs_n(vvv, r, c, scale):
        plot_vs_n(f"Val MSE", "val_scores", vvv, r, c, is_better='lower', scale=scale)
    def plot_train_score_vs_n(vvv, r, c, scale):
        plot_vs_n(f"Train MSE", "train_scores", vvv, r, c, is_better='lower', scale=scale)

    for c, vvv in enumerate(varying_variable_values):
        plot_test_score_vs_n(str(vvv), 1, c+1, scale=scale)
        plot_val_score_vs_n(str(vvv), 2, c+1, scale=scale)
        plot_train_score_vs_n(str(vvv), 3, c+1, scale=scale)

    return fig

In [96]:
fig = plot_results(varying_variable, varying_variable_values, scale='linear')
fig.update_layout(
    legend=dict(traceorder="normal", borderwidth=1),
    title=dict(x=0.5, text=f"Evaluation for {varying_variable} in {varying_variable_values}"), # \
            #    f"sigma {param_grid['sigma']} / alpha {param_grid['alpha']}"),
    width=800,
    height=1000,
)
fig.show()
if save:
    fig_file = filename + '.png'
    print(fig_file)
    fig.write_image(fig_file)

In [97]:
fig = plot_results(varying_variable, varying_variable_values, scale='log2')
fig.update_layout(
    legend=dict(traceorder="normal", borderwidth=1),
    title=dict(x=0.5, text=f"Evaluation for {varying_variable} in {varying_variable_values}"), # \
            #    f"sigma {param_grid['sigma']} / alpha {param_grid['alpha']}"),
    width=800,
    height=1000,
)
fig.show()
if save:
    fig_file = filename + '_log2.png'
    print(fig_file)
    fig.write_image(fig_file)

### Generalization / Overfitting

In [98]:
def plot_results_overfitting(varying_variable, varying_variable_values, scale='linear'):
    col_subplot_titles = ["Test Score", "Val Score", "Train Score", ]

    fig = make_subplots(
        rows=len(varying_variable_values),
        cols=len(col_subplot_titles),
        shared_yaxes=True,
        subplot_titles=col_subplot_titles + [None,] * len(varying_variable_values),
        vertical_spacing=0.1,
    )
    model_names = [model_name.split('_')[0] for model_name in model_configs.keys()]
    colors_list = colors.qualitative.Plotly * (
        len(model_names) // len(colors.qualitative.Plotly) + 1
    )
    colors_used = set()

    def plot(print_name, attr_name, vvv, r, c, is_better='higher', scale='log2'):
        """
        Args:
        - vvv: varying variable value
        """
        
        for result in results:
            model_name = result["model"]
            name_components = model_name.split('_') # E.g., Kernel-Thin_rbf -> Kernel-Thin, rbf
            if len(name_components) == 2:
                model_name_prefix, vv_name = name_components
                m = '0'
            else:
                model_name_prefix, m, vv_name = name_components        
            best_params = result["best_params_"]

            if vv_name != vvv:
                continue

            color = colors_list[model_names.index(model_name_prefix)]

            if scale == 'log2':
                y = np.log2(np.abs(result[attr_name]))
            elif scale == 'linear':
                y = np.abs(result[attr_name])

            trace = go.Box(
                x=[result['dataset']]*len(result[attr_name]),
                y=y,
                name=model_name_prefix,
                # opacity=0.5,
                legendgroup=model_name_prefix,
                line_color=color,
                offsetgroup=model_name_prefix,
                showlegend=color not in colors_used,
                boxmean=True,
            )

            fig.add_trace(trace, row=r, col=c)
            colors_used.add(color)

        if c == 1: fig.update_yaxes(title_text=f"{varying_variable}={vvv}", row=r, col=c)
        fig.update_xaxes(title_text="dataset", row=r, col=c)
        fig.update_layout(boxmode='group')

    def plot_test_score(vvv, r, c, scale):
        plot(f"Test MSE", "test_scores", vvv, r, c, is_better='lower', scale=scale)
    def plot_val_score(vvv, r, c, scale):
        plot(f"Val MSE", "val_scores", vvv, r, c, is_better='lower', scale=scale)
    def plot_train_score(vvv, r, c, scale):
        plot(f"Train MSE", "train_scores", vvv, r, c, is_better='lower', scale=scale)

    for r, vvv in enumerate(varying_variable_values):
        plot_test_score(str(vvv), r+1, 1, scale=scale)
        plot_val_score(str(vvv), r+1, 2, scale=scale)
        plot_train_score(str(vvv), r+1, 3, scale=scale)

    return fig

In [99]:
fig = plot_results_overfitting(varying_variable, varying_variable_values, scale='linear')
fig.update_layout(
    legend=dict(traceorder="normal", borderwidth=1),
    title=dict(x=0.5, text=f"Evaluation for {varying_variable} in {varying_variable_values}" \
            #    f"sigma {param_grid['sigma']} / alpha {param_grid['alpha']}"
               "<br>scale: linear"
               ),
    width=1000,
    height=600,
)
fig.show()

In [100]:
fig = plot_results_overfitting(varying_variable, varying_variable_values, scale='log2')
fig.update_layout(
    legend=dict(traceorder="normal", borderwidth=1),
    title=dict(x=0.5, text=f"Evaluation for {varying_variable} in {varying_variable_values}" \
            #    f"sigma {param_grid['sigma']} / alpha {param_grid['alpha']}"
               "<br>scale: log2"
               ),
    width=1000,
    height=600,
)
fig.show()